Nama : Astri Cahyaningtyas
==============

NIM : 1301154548
-----------------
Kelas : IF-39-02
------------------

Bangunlah sebuah sistem Q-learning untuk menemukan optimum policy sehingga Agent yang berada di posisi Start (1,1) mampu menemukan Goal yang berada di posisi (10,10) dengan mendapatkan Total Reward maksimum pada grid world dalam Figure 1 berikut ini. Data pada Figure 1 dapat dilihat di file DataTugasML3.txt. Pada kasus ini, Agent hanya bisa melakukan empat aksi: N, E, S, dan W yang secara berurutan menyatakan North (ke atas), East (ke kanan), South (ke bawah), dan West (ke kiri). Anda boleh menggunakan skema apapun dalam mengimplementasikan sebuah episode.

In [98]:
import numpy as np
import pandas as pd
import random
import matplotlib.pyplot as plt

Load Data Reward
=========

In [99]:
data_rw = pd.read_csv('DataTugasML3.txt', delimiter = '\t', header = None)
data_rw = np.array(rw).tolist()
data_rw

[[-1, -3, -5, -1, -3, -3, -5, -5, -1, 100],
 [-2, -1, -1, -4, -2, -5, -3, -5, -5, -5],
 [-3, -4, -4, -1, -3, -5, -5, -4, -3, -5],
 [-3, -5, -2, -5, -1, -4, -5, -1, -3, -4],
 [-4, -3, -3, -2, -1, -1, -1, -4, -3, -4],
 [-4, -2, -5, -2, -4, -5, -1, -2, -2, -4],
 [-4, -3, -2, -3, -1, -3, -4, -3, -1, -3],
 [-4, -2, -5, -4, -1, -4, -5, -5, -2, -4],
 [-2, -1, -1, -4, -1, -3, -5, -1, -4, -1],
 [-5, -3, -1, -2, -4, -3, -5, -2, -2, -2]]

Membuat array Reward
Agar setiap kotak terdefinisi kalau ke north ke kotak mana, kalau ke east ke kotak mana, kalau ke south ke kotak mana, kalau ke west ke kotak mana

In [103]:
def build_R(data_rw):
    xlen = len(data_rw)
    ylen = len(data_rw[0])

    r = pd.DataFrame(columns = ['north', 'east', 'south', 'west', 'this'])
    idx = 0 
    
    for i in range(ylen):
        for j in range(xlen):
            move = [float('-inf'),float('-inf'),float('-inf'),float('-inf'), rw[i][j]]
            if i>0:  #north
                move[0] = data_rw[i-1][j]
            if i<ylen-1: #south
                move[2] = data_rw[i+1][j]
            if j>0: #west
                move[3] = data_rw[i][j-1]
            if j<xlen-1: #east
                move[1] = data_rw[i][j+1]
            r.loc[idx] = move
            idx+=1
    return r

In [104]:
R = build_R(data_rw)
R = np.array(R)
R

array([[ -inf,   -3.,   -2.,  -inf,   -1.],
       [ -inf,   -5.,   -1.,   -1.,   -3.],
       [ -inf,   -1.,   -1.,   -3.,   -5.],
       [ -inf,   -3.,   -4.,   -5.,   -1.],
       [ -inf,   -3.,   -2.,   -1.,   -3.],
       [ -inf,   -5.,   -5.,   -3.,   -3.],
       [ -inf,   -5.,   -3.,   -3.,   -5.],
       [ -inf,   -1.,   -5.,   -5.,   -5.],
       [ -inf,  100.,   -5.,   -5.,   -1.],
       [ -inf,  -inf,   -5.,   -1.,  100.],
       [  -1.,   -1.,   -3.,  -inf,   -2.],
       [  -3.,   -1.,   -4.,   -2.,   -1.],
       [  -5.,   -4.,   -4.,   -1.,   -1.],
       [  -1.,   -2.,   -1.,   -1.,   -4.],
       [  -3.,   -5.,   -3.,   -4.,   -2.],
       [  -3.,   -3.,   -5.,   -2.,   -5.],
       [  -5.,   -5.,   -5.,   -5.,   -3.],
       [  -5.,   -5.,   -4.,   -3.,   -5.],
       [  -1.,   -5.,   -3.,   -5.,   -5.],
       [ 100.,  -inf,   -5.,   -5.,   -5.],
       [  -2.,   -4.,   -3.,  -inf,   -3.],
       [  -1.,   -4.,   -5.,   -3.,   -4.],
       [  -1.,   -1.,   -2.,   -

Membuat tabel Q(s,a)
===========

In [105]:
Q = np.zeros((100,5))
Q

array([[ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.],
       [ 0.,  

Membuat Transisi Matriks
=============

In [110]:
def build_trans(data_rw):
    xlen = len(data_rw)
    ylen = len(data_rw[0])
    
    t = pd.DataFrame(columns = ['north', 'east', 'south', 'west', 'none'])
    idx = 0 
    
    for i in range(ylen):
        for j in range(xlen):
            trans = [-1,-1,-1,-1, idx]
            if i>0: #north
                trans[0] = idx-xlen
            if i<ylen-1: #south
                trans[2] = idx+xlen
            if j>0: #west
                trans[3] = idx-1
            if j<xlen-1: #east
                trans[1] = idx+1
            t.loc[idx] = trans
            idx+=1
    return t

In [111]:
trans = build_trans(data_rw)
trans = np.array(trans)
trans

array([[-1, 1, 10, -1, 0],
       [-1, 2, 11, 0, 1],
       [-1, 3, 12, 1, 2],
       [-1, 4, 13, 2, 3],
       [-1, 5, 14, 3, 4],
       [-1, 6, 15, 4, 5],
       [-1, 7, 16, 5, 6],
       [-1, 8, 17, 6, 7],
       [-1, 9, 18, 7, 8],
       [-1, -1, 19, 8, 9],
       [0, 11, 20, -1, 10],
       [1, 12, 21, 10, 11],
       [2, 13, 22, 11, 12],
       [3, 14, 23, 12, 13],
       [4, 15, 24, 13, 14],
       [5, 16, 25, 14, 15],
       [6, 17, 26, 15, 16],
       [7, 18, 27, 16, 17],
       [8, 19, 28, 17, 18],
       [9, -1, 29, 18, 19],
       [10, 21, 30, -1, 20],
       [11, 22, 31, 20, 21],
       [12, 23, 32, 21, 22],
       [13, 24, 33, 22, 23],
       [14, 25, 34, 23, 24],
       [15, 26, 35, 24, 25],
       [16, 27, 36, 25, 26],
       [17, 28, 37, 26, 27],
       [18, 29, 38, 27, 28],
       [19, -1, 39, 28, 29],
       [20, 31, 40, -1, 30],
       [21, 32, 41, 30, 31],
       [22, 33, 42, 31, 32],
       [23, 34, 43, 32, 33],
       [24, 35, 44, 33, 34],
       [25, 36, 45, 34,

Membuat aksi yang dapat dilakukan oleh setiap kotak
===========================

0: north
1: east
2: south
3: west
4: none

In [117]:
def build_action(trans):
    act = []
    for i in range(len(trans)):
        current_act = []
        if (trans[i][0] != -1): #north
            current_act.append(0)
        if (trans[i][1] != -1): #east
            current_act.append(1)
        if (trans[i][2] != -1): #south
            current_act.append(2)
        if (trans[i][3] != -1): #west
            current_act.append(3)
        current_act.append(4)
        act.append(current_act)
    return act

In [118]:
act = build_action(trans)
act = np.array(act)
act

array([list([1, 2, 4]), list([1, 2, 3, 4]), list([1, 2, 3, 4]),
       list([1, 2, 3, 4]), list([1, 2, 3, 4]), list([1, 2, 3, 4]),
       list([1, 2, 3, 4]), list([1, 2, 3, 4]), list([1, 2, 3, 4]),
       list([2, 3, 4]), list([0, 1, 2, 4]), list([0, 1, 2, 3, 4]),
       list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]),
       list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]),
       list([0, 1, 2, 3, 4]), list([0, 2, 3, 4]), list([0, 1, 2, 4]),
       list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]),
       list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]),
       list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]), list([0, 2, 3, 4]),
       list([0, 1, 2, 4]), list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]),
       list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]),
       list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]), list([0, 1, 2, 3, 4]),
       list([0, 2, 3, 4]), list([0, 1, 2, 4]), list([0, 1, 2, 3

Eksplorasi dan Ekploitasi
==============

Alpha = 0.8
Episodes = 90000

In [148]:
alpha = 0.8
episodes = 100000
reward_list = []
for i in range(episodes):
    start_state = 90
    goal_state = 9
    current_state = start_state
    current_reward = R[current_state][4]
    while current_state != goal_state:
        #eksplorasi
        action = random.choice(act[current_state])
        next_state = trans[current_state][action]
        future_rewards = []
        for action_nxt in act[next_state]:
            future_rewards.append(Q[next_state][action_nxt])
            
        #update Q
        qstate = R[current_state][action] + alpha*max(future_rewards)
        Q[current_state][action] = qstate
        
        #eksploitasi
        current_state = next_state
        current_reward += R[current_state][4]
        if(current_state == goal_state):
            print('Episode {}, score : {}'.format(i, current_reward))
            reward_list.append(current_reward)

Episode 0, score : -1256.0
Episode 1, score : -3161.0
Episode 2, score : -777.0
Episode 3, score : -475.0
Episode 4, score : -3175.0
Episode 5, score : -2460.0
Episode 6, score : -399.0
Episode 7, score : -5146.0
Episode 8, score : -221.0
Episode 9, score : -1926.0
Episode 10, score : -1595.0
Episode 11, score : -5505.0
Episode 12, score : -453.0
Episode 13, score : -4.0
Episode 14, score : -1135.0
Episode 15, score : -1919.0
Episode 16, score : -742.0
Episode 17, score : -2821.0
Episode 18, score : -2928.0
Episode 19, score : -2550.0
Episode 20, score : -3700.0
Episode 21, score : -4165.0
Episode 22, score : -2283.0
Episode 23, score : -3870.0
Episode 24, score : -254.0
Episode 25, score : -401.0
Episode 26, score : -592.0
Episode 27, score : -6247.0
Episode 28, score : -2987.0
Episode 29, score : -6543.0
Episode 30, score : -3993.0
Episode 31, score : -2576.0
Episode 32, score : -1856.0
Episode 33, score : -2080.0
Episode 34, score : -2303.0
Episode 35, score : -3626.0
Episode 36, sc

Episode 332, score : -3042.0
Episode 333, score : -1109.0
Episode 334, score : -167.0
Episode 335, score : -1326.0
Episode 336, score : -2678.0
Episode 337, score : -1956.0
Episode 338, score : -172.0
Episode 339, score : -482.0
Episode 340, score : -4023.0
Episode 341, score : -5798.0
Episode 342, score : -1008.0
Episode 343, score : -2331.0
Episode 344, score : -367.0
Episode 345, score : -2983.0
Episode 346, score : -2189.0
Episode 347, score : -264.0
Episode 348, score : -298.0
Episode 349, score : -1164.0
Episode 350, score : -8700.0
Episode 351, score : -797.0
Episode 352, score : -612.0
Episode 353, score : -2956.0
Episode 354, score : -443.0
Episode 355, score : -864.0
Episode 356, score : -1543.0
Episode 357, score : -2434.0
Episode 358, score : -293.0
Episode 359, score : -3430.0
Episode 360, score : -497.0
Episode 361, score : -1574.0
Episode 362, score : -5249.0
Episode 363, score : -802.0
Episode 364, score : -941.0
Episode 365, score : -2697.0
Episode 366, score : -3241.0

Episode 660, score : -1287.0
Episode 661, score : -697.0
Episode 662, score : -1337.0
Episode 663, score : -1606.0
Episode 664, score : -1858.0
Episode 665, score : -3567.0
Episode 666, score : -3571.0
Episode 667, score : -4090.0
Episode 668, score : -2188.0
Episode 669, score : -616.0
Episode 670, score : -1000.0
Episode 671, score : -3061.0
Episode 672, score : -8087.0
Episode 673, score : -2978.0
Episode 674, score : -1531.0
Episode 675, score : -5735.0
Episode 676, score : -4121.0
Episode 677, score : -2542.0
Episode 678, score : -713.0
Episode 679, score : -775.0
Episode 680, score : -780.0
Episode 681, score : -1783.0
Episode 682, score : -1316.0
Episode 683, score : -482.0
Episode 684, score : -86.0
Episode 685, score : -1310.0
Episode 686, score : -730.0
Episode 687, score : -411.0
Episode 688, score : -314.0
Episode 689, score : -564.0
Episode 690, score : -515.0
Episode 691, score : -2429.0
Episode 692, score : -1717.0
Episode 693, score : -1139.0
Episode 694, score : -1249.

Episode 1001, score : -828.0
Episode 1002, score : -8543.0
Episode 1003, score : -884.0
Episode 1004, score : -628.0
Episode 1005, score : -1077.0
Episode 1006, score : -7325.0
Episode 1007, score : -1493.0
Episode 1008, score : -590.0
Episode 1009, score : -5615.0
Episode 1010, score : -777.0
Episode 1011, score : -5956.0
Episode 1012, score : -2127.0
Episode 1013, score : -1383.0
Episode 1014, score : -1849.0
Episode 1015, score : -338.0
Episode 1016, score : -4348.0
Episode 1017, score : -1073.0
Episode 1018, score : -881.0
Episode 1019, score : -205.0
Episode 1020, score : -4230.0
Episode 1021, score : -124.0
Episode 1022, score : -495.0
Episode 1023, score : -1477.0
Episode 1024, score : -1136.0
Episode 1025, score : -1671.0
Episode 1026, score : -8049.0
Episode 1027, score : -539.0
Episode 1028, score : -1961.0
Episode 1029, score : -4935.0
Episode 1030, score : -2471.0
Episode 1031, score : -2163.0
Episode 1032, score : -667.0
Episode 1033, score : -2593.0
Episode 1034, score : 

Episode 1310, score : -4919.0
Episode 1311, score : -395.0
Episode 1312, score : -254.0
Episode 1313, score : -1103.0
Episode 1314, score : -1730.0
Episode 1315, score : -2298.0
Episode 1316, score : -1010.0
Episode 1317, score : -5077.0
Episode 1318, score : -937.0
Episode 1319, score : -1244.0
Episode 1320, score : -235.0
Episode 1321, score : -2560.0
Episode 1322, score : -2608.0
Episode 1323, score : -4400.0
Episode 1324, score : -1350.0
Episode 1325, score : -2756.0
Episode 1326, score : -2388.0
Episode 1327, score : -801.0
Episode 1328, score : -6425.0
Episode 1329, score : -410.0
Episode 1330, score : -1503.0
Episode 1331, score : -1944.0
Episode 1332, score : -1375.0
Episode 1333, score : -780.0
Episode 1334, score : -1970.0
Episode 1335, score : -592.0
Episode 1336, score : -1310.0
Episode 1337, score : -1374.0
Episode 1338, score : -1464.0
Episode 1339, score : -3275.0
Episode 1340, score : -3497.0
Episode 1341, score : -1287.0
Episode 1342, score : -1054.0
Episode 1343, scor

...

Episode 97111, score : -3219.0
Episode 97112, score : -1891.0
Episode 97113, score : -1932.0
Episode 97114, score : -4443.0
Episode 97115, score : -331.0
Episode 97116, score : -3861.0
Episode 97117, score : -478.0
Episode 97118, score : -696.0
Episode 97119, score : -2408.0
Episode 97120, score : -3314.0
Episode 97121, score : -637.0
Episode 97122, score : -1137.0
Episode 97123, score : -3027.0
Episode 97124, score : -1458.0
Episode 97125, score : -491.0
Episode 97126, score : -1810.0
Episode 97127, score : -380.0
Episode 97128, score : -669.0
Episode 97129, score : -5529.0
Episode 97130, score : -1517.0
Episode 97131, score : -1053.0
Episode 97132, score : -6821.0
Episode 97133, score : -5343.0
Episode 97134, score : -1913.0
Episode 97135, score : -3023.0
Episode 97136, score : -1305.0
Episode 97137, score : -2677.0
Episode 97138, score : -5013.0
Episode 97139, score : -1103.0
Episode 97140, score : -2991.0
Episode 97141, score : -2729.0
Episode 97142, score : -339.0
Episode 97143, s

Episode 97635, score : -1019.0
Episode 97636, score : -1122.0
Episode 97637, score : -2939.0
Episode 97638, score : -2381.0
Episode 97639, score : -814.0
Episode 97640, score : -654.0
Episode 97641, score : -1079.0
Episode 97642, score : -354.0
Episode 97643, score : -2104.0
Episode 97644, score : -1587.0
Episode 97645, score : -1504.0
Episode 97646, score : -7388.0
Episode 97647, score : -767.0
Episode 97648, score : -731.0
Episode 97649, score : -1186.0
Episode 97650, score : -2354.0
Episode 97651, score : -3176.0
Episode 97652, score : -829.0
Episode 97653, score : -1034.0
Episode 97654, score : -2670.0
Episode 97655, score : -1057.0
Episode 97656, score : -532.0
Episode 97657, score : -716.0
Episode 97658, score : -1695.0
Episode 97659, score : -1537.0
Episode 97660, score : -2509.0
Episode 97661, score : -165.0
Episode 97662, score : -513.0
Episode 97663, score : -844.0
Episode 97664, score : -360.0
Episode 97665, score : -2169.0
Episode 97666, score : -1064.0
Episode 97667, score

Episode 98183, score : -3255.0
Episode 98184, score : -63.0
Episode 98185, score : -795.0
Episode 98186, score : -1459.0
Episode 98187, score : -12041.0
Episode 98188, score : -356.0
Episode 98189, score : -5674.0
Episode 98190, score : -1343.0
Episode 98191, score : -338.0
Episode 98192, score : -663.0
Episode 98193, score : -4406.0
Episode 98194, score : -1891.0
Episode 98195, score : -3271.0
Episode 98196, score : -590.0
Episode 98197, score : -1247.0
Episode 98198, score : -4318.0
Episode 98199, score : -597.0
Episode 98200, score : -4216.0
Episode 98201, score : -825.0
Episode 98202, score : -6900.0
Episode 98203, score : -1146.0
Episode 98204, score : -7071.0
Episode 98205, score : -3695.0
Episode 98206, score : -2224.0
Episode 98207, score : -819.0
Episode 98208, score : -899.0
Episode 98209, score : -940.0
Episode 98210, score : -844.0
Episode 98211, score : -170.0
Episode 98212, score : -3304.0
Episode 98213, score : -1360.0
Episode 98214, score : -557.0
Episode 98215, score :

Episode 98749, score : -808.0
Episode 98750, score : -1709.0
Episode 98751, score : -2710.0
Episode 98752, score : -70.0
Episode 98753, score : -1127.0
Episode 98754, score : -3567.0
Episode 98755, score : -316.0
Episode 98756, score : -33.0
Episode 98757, score : -809.0
Episode 98758, score : -4563.0
Episode 98759, score : -2967.0
Episode 98760, score : -1183.0
Episode 98761, score : -1122.0
Episode 98762, score : -1605.0
Episode 98763, score : -317.0
Episode 98764, score : -2638.0
Episode 98765, score : -1301.0
Episode 98766, score : -246.0
Episode 98767, score : -419.0
Episode 98768, score : -1348.0
Episode 98769, score : -893.0
Episode 98770, score : -2060.0
Episode 98771, score : -130.0
Episode 98772, score : -1104.0
Episode 98773, score : -4785.0
Episode 98774, score : -3700.0
Episode 98775, score : -5321.0
Episode 98776, score : -759.0
Episode 98777, score : -1048.0
Episode 98778, score : -3733.0
Episode 98779, score : -1758.0
Episode 98780, score : -6304.0
Episode 98781, score 

Episode 99322, score : -202.0
Episode 99323, score : -1369.0
Episode 99324, score : -758.0
Episode 99325, score : -356.0
Episode 99326, score : -221.0
Episode 99327, score : -1463.0
Episode 99328, score : -3158.0
Episode 99329, score : -1555.0
Episode 99330, score : -1029.0
Episode 99331, score : -4309.0
Episode 99332, score : -151.0
Episode 99333, score : -7614.0
Episode 99334, score : -3761.0
Episode 99335, score : -3959.0
Episode 99336, score : -368.0
Episode 99337, score : -2221.0
Episode 99338, score : -946.0
Episode 99339, score : -360.0
Episode 99340, score : -196.0
Episode 99341, score : -2025.0
Episode 99342, score : -270.0
Episode 99343, score : -2014.0
Episode 99344, score : -2709.0
Episode 99345, score : -2609.0
Episode 99346, score : -1751.0
Episode 99347, score : -1135.0
Episode 99348, score : -920.0
Episode 99349, score : -2213.0
Episode 99350, score : -4953.0
Episode 99351, score : -7268.0
Episode 99352, score : -1368.0
Episode 99353, score : -2280.0
Episode 99354, scor

In [157]:
Q_update = pd.DataFrame(columns = ['north', 'east', 'south', 'west', 'none'])

In [158]:
for i in range(len(Q)):
    Q_update.loc[i] = Q[i]

In [159]:
Q_update

north        east      south       west       none
0     0.000000    3.213581   1.048692   0.000000   1.570865
1     0.000000    7.766976   3.810865   1.570865   3.213581
2     0.000000   15.958720   6.013581   3.213581   7.766976
3     0.000000   21.198400   8.766976   7.766976  15.958720
4     0.000000   30.248000  14.958720  15.958720  21.198400
5     0.000000   41.560000  19.198400  21.198400  30.248000
6     0.000000   58.200000  30.248000  30.248000  41.560000
7     0.000000   79.000000  41.560000  41.560000  58.200000
8     0.000000  100.000000  58.200000  58.200000  79.000000
9     0.000000    0.000000   0.000000   0.000000   0.000000
10    1.570865    3.810865  -2.161047   0.000000   1.048692
11    3.213581    6.013581  -0.951308   1.048692   3.810865
12    7.766976    8.766976   0.938865   3.810865   6.013581
13   15.958720   14.958720   6.173581   6.013581   8.766976
14   21.198400   19.198400   8.966976   8.766976  14.958720
15   30.248000   30.248000  10.742720  14.958720  19.198400
16   41.560000   41.560000  19.678400  19.198400  30.248000
17   58.200000   58.200000  30.848000  30.248000  41.560000
18   79.000000   75.000000  43.560000  41.560000  58.200000
19  100.000000    0.000000  55.000000  58.200000  75.000000
20    1.048692   -0.951308  -4.728837   0.000000  -2.161047
21    3.810865    0.938865  -5.761047  -2.161047  -0.951308
22    6.013581    6.173581  -1.248908  -0.951308   0.938865
23    8.766976    8.966976  -0.061135   0.938865   6.173581
24   14.958720   10.742720   6.173581   6.173581   8.966976
25   19.198400   19.678400   7.666176   8.966976  10.742720
26   30.248000   30.848000  14.582720  10.742720  19.678400
27   41.560000   43.560000  24.478400  19.678400  30.848000
28   58.200000   55.000000  31.848000  30.848000  43.560000
29   75.000000    0.000000  40.000000  43.560000  55.000000
..         ...         ...        ...        ...        ...
70   -9.238714   -6.000000  -6.000000   0.000000  -8.800000
71   -6.548393   -8.548393  -5.000000  -8.800000  -6.000000
72   -4.435491   -5.219491  -5.000000  -6.000000  -8.548393
73   -3.044363   -1.524363  -5.775593  -8.548393  -5.219491
74   -0.655454   -4.775454  -2.219491  -5.219491  -1.524363
75   -0.969318   -2.969318  -4.775593  -1.524363  -4.775454
76    2.538353    0.943153  -4.556382  -4.775454  -2.969318
77    6.428941    7.428941   0.554522  -2.969318   0.943153
78   11.786176    5.376000   1.943153   0.943153   7.428941
79   11.720000    0.000000   3.300800   7.428941   5.376000
80   -8.800000   -5.000000  -9.800000   0.000000  -6.000000
81   -6.000000   -5.000000  -7.000000  -6.000000  -5.000000
82   -8.548393   -5.775593  -5.000000  -5.000000  -5.000000
83   -5.219491   -2.219491  -6.000000  -5.000000  -5.775593
84   -1.524363   -4.775593  -5.775593  -5.775593  -2.219491
85   -4.775454   -4.556382  -6.820474  -2.219491  -4.775593
86   -2.969318    0.554522  -6.245106  -4.775593  -4.556382
87    0.943153    1.943153  -1.556382  -4.556382   0.554522
88    7.428941    3.300800  -0.445478   0.554522   1.943153
89    5.376000    0.000000   0.640640   1.943153   3.300800
90   -6.000000   -7.000000   0.000000   0.000000  -9.800000
91   -5.000000   -5.000000   0.000000  -9.800000  -7.000000
92   -5.000000   -6.000000   0.000000  -7.000000  -5.000000
93   -5.775593   -5.775593   0.000000  -5.000000  -6.000000
94   -2.219491   -6.820474   0.000000  -6.000000  -5.775593
95   -4.775593   -6.245106   0.000000  -5.775593  -6.820474
96   -4.556382   -1.556382   0.000000  -6.820474  -6.245106
97    0.554522   -0.445478   0.000000  -6.245106  -1.556382
98    1.943153    0.640640   0.000000  -1.556382  -0.445478
99    3.300800    0.000000   0.000000  -0.445478   0.640640

[100 rows x 5 columns]

In [160]:
max(reward_list)

36.0

Reward = 36
======